In [3]:
import sys
import os

# Assuming your project directory is one level up from the Jupyter notebook
sys.path.insert(0, os.path.abspath('../..'))

import lightning as L
import matplotlib
import numpy as np
import pandas as pd
import multiprocessing
from src.pipelines.trainers.trainerWrapper import TrainerWrapper
from src.util.conditional_early_stopping import ConditionalEarlyStopping
from src.util.power_splitter import PowerSplitter
from src.util.error import NRMSE, MNLL
from src.util.plotly import plot_results

from src.pipelines.cleaners.temp_cleaner import TempCleaner
from src.pipelines.models.lstm import LSTM
from src.pipelines.normalizers.min_max_normalizer import MinMaxNormalizer
from src.pipelines.sequencers.time_sequencer import TimeSequencer
from src.pipelines.splitters.std_splitter import StdSplitter
from src.pipelines.tuners.std_tuner_wrapper import StdTunerWrapper
from src.pipelines.optimizers.optimizer import OptimizerWrapper

from src.pipelines.deterministic_pipeline import DeterministicPipeline
from src.pipelines.monte_carlo_pipeline import MonteCarloPipeline
from src.pipelines.ensemble_pipeline import EnsemblePipeline
from src.pipelines.probabilistic_pipeline import ProbabilisticPipeline

from src.util.evaluator import Evaluator

import torch.optim as optim

matplotlib.use("Agg")

MODEL_PATH = 'model_saves/ex14_model'
NUM_WORKERS = multiprocessing.cpu_count()
TARGET_COLUMN = 2
TIMESTAMP = "Timestamp"
POWER     = "PowerConsumption"

# Hyper parameters
# Model
input_size = 4
time_horizon = 4
hidden_size = 32
num_epochs = 1000
seq_len = 96
num_layers = 2
 
# MC ONLY
inference_samples = 50

# Training
dropout = 0.50
gradient_clipping = 0
early_stopping_threshold = 0.15

num_ensembles = 5

# Flexibility
flex_confidence = 0.90
temp_boundary = 0.1
error = 0

# Controlled by tuner
batch_size = 128
learning_rate = 0.005

# Data Split
train_days = 16
val_days = 2
test_days = 2

# ON / OFF Power Limits
off_limit_w = 88
on_limit_w = 963

consecutive_points = 3

uk_path = "../../src/data_preprocess/dataset/UKDATA_cleaned.csv"

clean_in_low = 10
clean_in_high = 30
clean_out_low = -50
clean_out_high = 50
clean_pow_low = 0
clean_delta_temp = 15

In [2]:
assert time_horizon > 0, "Time horizon must be a positive integer"
    
df = pd.read_csv(uk_path)

cleaner = TempCleaner(clean_pow_low, clean_in_low, clean_in_high, clean_out_low, clean_out_high, clean_delta_temp)
splitter = StdSplitter(train_days, val_days, test_days)
    
model = LSTM(hidden_size, num_layers, input_size, time_horizon, dropout)
trainer = TrainerWrapper(L.Trainer, 
                         max_epochs=num_epochs, 
                         callbacks=[ConditionalEarlyStopping(threshold=early_stopping_threshold)], 
                         gradient_clip_val=gradient_clipping)
optimizer = OptimizerWrapper(optim.Adam, model, lr=learning_rate)

model = MonteCarloPipeline.Builder() \
    .add_data(df) \
    .set_cleaner(cleaner) \
    .set_normalizer_class(MinMaxNormalizer) \
    .set_splitter(splitter) \
    .set_sequencer_class(TimeSequencer) \
    .set_target_column(TARGET_COLUMN) \
    .set_model(model) \
    .set_optimizer(optimizer) \
    .set_batch_size(batch_size) \
    .set_seq_len(seq_len) \
    .set_worker_num(NUM_WORKERS) \
    .set_error(NRMSE) \
    .set_trainer(trainer) \
    .set_tuner_class(StdTunerWrapper) \
    .set_inference_samples(inference_samples) \
    .set_test_error(MNLL) \
    .build()

model = EnsemblePipeline.Builder() \
        .set_pipeline(model) \
        .set_num_ensembles(num_ensembles) \
        .build()

model.fit()
model.save(MODEL_PATH)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Train

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]



  | Name  | Type | Params | Mode 
---------------------------------------
0 | model | LSTM | 13.4 K | train
---------------------------------------
13.4 K    Trainable params
0         Non-trainable params
13.4 K    Total params
0.054     Total estimated model params size (MB)
3         Modules in train mode
0         Modules in eval mode



  | Name  | Type | Params | Mode 
---------------------------------------
0 | model | LSTM | 13.4 K | train
---------------------------------------
13.4 K    Trainable params
0         Non-trainable params
13.4 K    Total params
0.054     Total estimated model params size (MB)
3         Modules in train mode
0         Modules in eval mode


Restoring states from the checkpoint path at /home/vind/P5/experimentation/experiments/iter1/.scale_batch_size_7f00cd1d-6467-46a8-ab19-5d70a6070cf3.ckpt


Restored all states from the checkpoint at /home/vind/P5/experimentation/experiments/iter1/.scale_batch_size_7f00cd1d-6467-46a8-ab19-5d70a6070cf3.ckpt
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Sanity Checking DataLoader 0:   0%|          | 0/9 [00:00<?, ?it/s]


  | Name  | Type | Params | Mode 
---------------------------------------
0 | model | LSTM | 13.4 K | train
---------------------------------------
13.4 K    Trainable params
0         Non-trainable params
13.4 K    Total params
0.054     Total estimated model params size (MB)
3         Modules in train mode
0         Modules in eval mode


Epoch 25:  30%|██▉       | 21/71 [00:03<00:07,  6.77it/s, v_num=70, train_loss_step=0.274, val_loss=0.277, train_loss_epoch=0.253]       
saving to model_saves/ex14_model


In [4]:

df = pd.read_csv(uk_path)

cleaner = TempCleaner(clean_pow_low, clean_in_low, clean_in_high, clean_out_low, clean_out_high, clean_delta_temp)
splitter = StdSplitter(train_days, val_days, test_days)
    
model = LSTM(hidden_size, num_layers, input_size, time_horizon, dropout)
trainer = TrainerWrapper(L.Trainer, 
                         max_epochs=num_epochs, 
                         callbacks=[ConditionalEarlyStopping(threshold=early_stopping_threshold)], 
                         gradient_clip_val=gradient_clipping)
optimizer = OptimizerWrapper(optim.Adam, model, lr=learning_rate)

model = DeterministicPipeline.Builder() \
    .add_data(df) \
    .set_cleaner(cleaner) \
    .set_normalizer_class(MinMaxNormalizer) \
    .set_splitter(splitter) \
    .set_sequencer_class(TimeSequencer) \
    .set_target_column(TARGET_COLUMN) \
    .set_model(model) \
    .set_optimizer(optimizer) \
    .set_batch_size(batch_size) \
    .set_seq_len(seq_len) \
    .set_worker_num(NUM_WORKERS) \
    .set_error(NRMSE) \
    .set_trainer(trainer) \
    .set_tuner_class(StdTunerWrapper) \
    .build()

model = EnsemblePipeline.Builder() \
        .set_pipeline(model) \
        .set_num_ensembles(num_ensembles) \
        .build()

model.load(MODEL_PATH)
model.test()

plot_results(model.get_predictions(), model.get_actuals(), model.get_timestamps(), time_horizon)

model.eval()

ps = PowerSplitter(splitter.get_test(cleaner.clean(df)), TIMESTAMP, POWER)

on_df = ps.get_mt_power(on_limit_w, consecutive_points)
off_df = ps.get_lt_power(off_limit_w, consecutive_points)

def normalize_and_convert_dates(data):
    data[:, 0] = pd.to_datetime(data[:, 0]).astype(int) / 10**9
    temp = MinMaxNormalizer(data.astype(float)).normalize()
    return temp[0]

on_data = np.array(on_df)
on_data = normalize_and_convert_dates(on_data)

off_data = np.array(off_df)
off_data = normalize_and_convert_dates(off_data)

evaluator = Evaluator(model, error, temp_boundary)

print("Calculating On set...")
evaluator.init_predictions(on_data, seq_len, time_horizon, TARGET_COLUMN, confidence=0.95) 
print(f"On Mafe: {evaluator.evaluate(lambda a, b: abs(a - b))}") 
print(f"On Maofe: {evaluator.evaluate(lambda a, b: abs(max(a - b, 0)))}")
print(f"On Maufe: {evaluator.evaluate(lambda a, b: abs(min(a - b, 0)))}")

print("Calculating Off set...")
evaluator.init_predictions(off_data, seq_len, time_horizon, TARGET_COLUMN, confidence=0.95)
print(f"Off Mafe: {evaluator.evaluate(lambda a, b: abs(a - b))}")
print(f"Off Maofe: {evaluator.evaluate(lambda a, b: abs(max(a - b, 0)))}")
print(f"Off Maufe: {evaluator.evaluate(lambda a, b: abs(min(a - b, 0)))}")

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Train

Testing: |          | 0/? [00:00<?, ?it/s]
Testing: |          | 0/? [00:00<?, ?it/s]
Testing DataLoader 0:   0%|          | 0/9 [00:00<?, ?it/s]
Testing: |          | 0/? [00:00<?, ?it/s]
Testing: |          | 7/? [00:00<00:00, 18.38it/s]
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
     test_loss_epoch        0.1122332513332367
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
     test_loss_epoch

Calculating On set...


On Mafe: 0.0
On Maofe: 0.0
On Maufe: 0.0
Calculating Off set...


Off Mafe: 1.2889952153110047
Off Maofe: 0.03923444976076555
Off Maufe: 1.2497607655502392
